# Imports

In [1]:
import glob
import os
from typing import Dict, List
import warnings
from lightgbm import LGBMClassifier
warnings.filterwarnings('ignore')
import numpy as np
import pandas as pd
import scipy as sp
import scipy.signal
import scipy.stats
from sklearn.model_selection import GroupKFold
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV, LeaveOneOut
from sklearn.svm import SVC
from utils import variance_thresholding, standardize, calculate_metrics, calculate_metrics_statistics, DatasetWin, calculate_metrics_from_df
import lightgbm as lgb
from lightgbm_utils import lightgbm_fit_binary

In [2]:
# parameters for Welch's method for estimating power spectrum

NPERSEG = 60                    # length of segment
NOVERLAP = int(0.75 * NPERSEG)  # overlap of segments
NFFT = NPERSEG                  # length of FFT
WINDOW = "hann"                 # window function type

# parameters for saving data
PROCESSED_DATA_DIR = "processed_data"
DEPRESJON_PREFIX = "depresjon"
PSYKOSE_PREFIX = "psykose"
HYPERAKTIV_PREFIX = "hyperaktiv"
MAIN_RESULTS_DIR = "results"
DAY_WINDOWS_DIR = "day_windows"
WINDOWS_DIR = "windows"
#DAY_NIGHT_HOURS = (8, 21) # (6, 22) / (8, 21)
DAY_NIGHT_HOURS = [(8, 21), (6, 22)]
#day_night_format = f'{DAY_NIGHT_HOURS[0]}_{DAY_NIGHT_HOURS[1]}' # "6, 22" / "8, 21"

# Manual feature extraction

## Helper functions

In [3]:
def basic_data_cleaning(data: List[List[pd.DataFrame]]) -> List[List[pd.DataFrame]]:
    """
    Assumes DataFrames with "timestamp", "date" and "activity" columns.
    
    Performs cleaning operations:
    - Format "timestamp" to YYYY-MM-DD HH:MM:SS
    - Drop redundant "date" column
    - Convert "activity" to float32
    
    :param data: list of DataFrames
    :returns: list of cleaned DataFrames
    """
    data = [df.copy() for df in data]  # create copy to avoid side effects
    for patient in data:
        for df in patient:
            # Convert and enforce the desired timestamp format
            df["timestamp"] = pd.to_datetime(df["timestamp"], dayfirst=False)
            df["timestamp"] = df["timestamp"].dt.strftime("%Y-%m-%d %H:%M:%S")
            
            # Drop "date" column if it exists
            if "date" in df.columns:
                df.drop("date", axis=1, inplace=True)
            
            # Ensure "activity" column is float32
            df["activity"] = df["activity"].astype(np.float32)
    
    return data


def get_day_part(df: pd.DataFrame, part: str) -> pd.DataFrame:
    """
    For given DataFrame with "timestamp" column returns only those rows that
    correspond to the chosen part of day.
    
    Parts are "day" and "night", defined as:
    - "day": [8:00, 21:00)
    - "night": [21:00, 8:00)
    
    :param df: DataFrame to select rows from
    :param part: part of day, either "day" or "night"
    :param hour_day_start: hour when day start (default 8)
    :param hour_day_end: hour when day ends (starts night) (default 21)
    :returns: DataFrame, subset of rows of df
    """
    if part == "day":
        df = df.loc[(df["timestamp"].dt.hour >= DAY_NIGHT_HOURS[0]) &
                    (df["timestamp"].dt.hour < DAY_NIGHT_HOURS[1])]
    elif part == "night":
        df = df.loc[(df["timestamp"].dt.hour >= DAY_NIGHT_HOURS[1]) |
                    (df["timestamp"].dt.hour < DAY_NIGHT_HOURS[0])]
    else:
        raise ValueError(f'Part should be "day" or "night", got "{part}"')
        
    return df


def fill_missing_activity(df: pd.DataFrame, freq: str = "min") -> pd.DataFrame:
    """
    Fill missing activity values by resampling based on given frequency.
    
    :param df: DataFrame with 'timestamp' and 'activity' columns.
    :param freq: Resampling frequency (default: minute).
    :return: DataFrame with missing values filled.
    """
    df = df.copy() # create copy to avoid side effects
  
    df["timestamp"] = pd.to_datetime(df["timestamp"])

    df.set_index("timestamp", inplace=True)

    # resample to the basic frequency, i.e. minute; this will create NaNs for
    # any rows that may be missing
    df = df.resample(freq).mean()
    
    # recreate index and "timestamp" column
    df.reset_index(inplace=True)

    # fill any NaNs with mean activity value
    df["activity"] = df["activity"].fillna(df["activity"].mean())
    
    return df


def resample(df: pd.DataFrame, freq: str = "H") -> pd.DataFrame:
    """
    Resamples time series DataFrame with given frequency, aggregating each
    segment with a mean.

    :param df: DataFrame with "timestamp" and "activity" columns
    :param freq: resampling frequency passed to Pandas resample() function
    :returns: DataFrame with "timestamp" and "activity" columns
    """
    df = df.copy()  # create copy to avoid side effects
    
    # group with given frequency
    df = df.resample(freq, on="timestamp").mean()

    # recreate "timestamp" column
    df = df.reset_index()

    return df


def proportion_of_zeros(x: np.ndarray) -> float:
    """
    Calculates proportion of zeros in given array, i.e. number of zeros divided
    by length of array.
    
    :param x: 1D Numpy array
    :returns: proportion of zeros
    """
    # we may be dealing with floating numbers, we can't use direct comparison
    zeros_count = np.sum(np.isclose(x, 0))
    return zeros_count / len(x)


def power_spectral_density(df: pd.DataFrame) -> np.ndarray:
    """
    Calculates power spectral density (PSD) from "activity" column of a
    DataFrame.
    
    :param df: DataFrame with "activity" column
    :returns: 1D Numpy array with power spectral density
    """

    activity = df["activity"].values
    nperseg = min(NPERSEG, len(activity))  # Ensure nperseg doesn't exceed data length
    noverlap = int(0.75 * nperseg) 
    
    psd = scipy.signal.welch(
        x=activity,
        fs=(1/60),
        nperseg=nperseg,
        noverlap=noverlap,
        nfft=NFFT,
        window=WINDOW,
        scaling="density"
    )[1]
    return psd


def spectral_flatness(df: pd.DataFrame) -> float:
    """
    Calculates spectral flatness of a signal, i.e. a geometric mean of the
    power spectrum divided by the arithmetic mean of the power spectrum.
    
    If some frequency bins in the power spectrum are close to zero, they are
    removed prior to calculation of spectral flatness to avoid calculation of
    log(0).
    
    :param df: DataFrame with "activity" column
    :returns: spectral flatness value
    """

    activity = df["activity"].values
    nperseg = min(NPERSEG, len(activity))  # Ensure nperseg doesn't exceed data length
    noverlap = int(0.75 * nperseg) 

    power_spectrum = scipy.signal.welch(
        activity,
        fs=(1/60),
        nperseg=nperseg,
        noverlap=noverlap,
        nfft=NFFT,
        window=WINDOW,
        scaling="spectrum"
    )[1]
    
    non_zeros_mask = ~np.isclose(power_spectrum, 0)
    power_spectrum = power_spectrum[non_zeros_mask]
    
    return scipy.stats.gmean(power_spectrum) / power_spectrum.mean()

## Feature extraction

In [4]:
def extract_time_features(df: pd.DataFrame) -> pd.DataFrame:
    """
    Extracts features from activity signal in time domain.
    
    :param df_resampled: DataFrame with "activity" column
    :returns: DataFrame with a single row representing features
    """
    X = df["activity"].values
    
    features = {
        "minimum": np.min(X),
        "maximum": np.max(X),
        "mean": np.mean(X),
        "median": np.median(X),
        "variance": np.var(X, ddof=1),  # apply Bessel's correction
        "kurtosis": sp.stats.kurtosis(X),
        "skewness": sp.stats.skew(X),
        "coeff_of_var": sp.stats.variation(X),
        "iqr": sp.stats.iqr(X),
        "trimmed_mean": sp.stats.trim_mean(X, proportiontocut=0.1),
        "entropy": sp.stats.entropy(X, base=2),
        "proportion_of_zeros": proportion_of_zeros(X)
    }
    
    return pd.DataFrame([features])

In [5]:
def extract_frequency_features(df: pd.DataFrame) -> pd.DataFrame:
    """
    Extracts features from activity signal in frequency domain, i.e. calculated
    from its Power Spectral Density (PSD).
    
    :param df: DataFrame with "activity" column
    :returns: DataFrame with a single row representing features
    """
    X = power_spectral_density(df)
    
    features = {
        "minimum": np.min(X),
        "maximum": np.max(X),
        "mean": np.mean(X),
        "median": np.median(X),
        "variance": np.var(X),
        "kurtosis": sp.stats.kurtosis(X),
        "skewness": sp.stats.skew(X),
        "coeff_of_var": sp.stats.variation(X),
        "iqr": sp.stats.iqr(X),
        "trimmed_mean": sp.stats.trim_mean(X, proportiontocut=0.1),
        "entropy": sp.stats.entropy(X, base=2),
        "spectral_flatness": spectral_flatness(df)
    }
    
    return pd.DataFrame([features])

In [6]:
def extract_features_for_dataframes(dfs: List[List[pd.DataFrame]], is_condition: bool = True, freq: str = "H") \
        -> Dict[str, pd.DataFrame]:
    """
    Calculates time and frequency features for given DataFrames. Uses given
    frequency for resampling.
    
    Calculates features separately for:
    - full 24hs
    - days: default [8:00, 21:00)
    - nights: default [21:00, 8:00)
    
    :param dfs: list of lists of DataFrames to extract features from; each one has to
    have "timestamp" and "activity" columns
    :param freq: resampling frequency
    :returns: dictionary with keys "full_24h", "day" and "night", corresponding
    to features from given parts of day
    """
    full_dfs = basic_data_cleaning(dfs)
    full_dfs = [[fill_missing_activity(df) for df in patient] for patient in full_dfs]
    full_dfs = [[resample(df, freq=freq) for df in patient] for patient in full_dfs]
    night_dfs = [[get_day_part(df, part="night") for df in patient] for patient in full_dfs]
    day_dfs = [[get_day_part(df, part="day") for df in patient] for patient in full_dfs]

    datasets = {}
    
    
    for part, list_of_dfs in [("full_24h", full_dfs), ("night", night_dfs), ("day", day_dfs)]:
        features = []
        for patient in range(len(list_of_dfs)):
            for day in range(len(list_of_dfs[patient])):
                time_features = extract_time_features(list_of_dfs[patient][day])
                freq_features = extract_frequency_features(list_of_dfs[patient][day])
    
                merged_features = pd.merge(
                    time_features,
                    freq_features,
                    left_index=True,
                    right_index=True,
                    suffixes=("_time", "_freq")
                )
                merged_features['day'] = day + 1
                merged_features['patient_id'] = patient + 1
                if is_condition:
                    merged_features['class'] = 1
                else:
                    merged_features['class'] = 0
                features.append(merged_features)
    
        datasets[part] = pd.concat(features)
        datasets[part].reset_index(drop=True, inplace=True)
    
    return datasets

## Hyperaktiv

In [7]:
path = os.path.join(PROCESSED_DATA_DIR, DAY_WINDOWS_DIR, "hyperaktiv")
dataset = DatasetWin(dirpath=path, sep=',')
condition = dataset.condition
control = dataset.control

In [ ]:
condition_parts_dfs = extract_features_for_dataframes(condition, is_condition=True, freq="H")
control_parts_dfs = extract_features_for_dataframes(control, is_condition=False, freq="H")

datasets = {}

for part in ["full_24h", "night", "day"]:
    condition_df = condition_parts_dfs[part]
    control_df = control_parts_dfs[part]
    max_patient = condition_df['patient_id'].max()
    control_df['patient_id'] += max_patient # changing numeration of patients
    entire_df = pd.concat([condition_df, control_df], ignore_index=True)
    datasets[part] = entire_df

In [219]:
# save windows features
os.makedirs(PROCESSED_DATA_DIR, exist_ok=True)
os.makedirs(os.path.join(PROCESSED_DATA_DIR, WINDOWS_DIR), exist_ok=True)
for part, df in datasets.items():
    for hours in DAY_NIGHT_HOURS:
        filename = f"{HYPERAKTIV_PREFIX}_{hours[0]}_{hours[1]}_{part}.csv"
        filepath = os.path.join(PROCESSED_DATA_DIR, WINDOWS_DIR, filename)
        df.to_csv(filepath, index=False, header=True)

In [9]:

for hours in DAY_NIGHT_HOURS:
    filename = f"{HYPERAKTIV_PREFIX}_{hours[0]}_{hours[1]}.csv"
    print(filename)

hyperaktiv_8_21.csv
hyperaktiv_6_22.csv


# Classification

## Classifiers, parameters, constants

In [5]:
classifiers = {
    "GBM": LGBMClassifier(
        objective='binary',
        metric=['auc', 'binary_logloss'],
        force_col_wise=True,
        verbosity=-1
    ),
    "LR": LogisticRegression(
        penalty="elasticnet",
        random_state=0,
        solver="saga",
        max_iter=5000
    ),
    "SVM": SVC(
        kernel="poly",
        cache_size=512,
        max_iter=5000
    ),
    "RF": RandomForestClassifier(
        n_estimators=500,
        criterion="entropy"
    )
}


param_grids = {
    "GBM":{
        'num_leaves': [25, 50, 100, 250, 500],
        'max_depth': [5, 10, 15, 20, 25],
        'learning_rate': [0.01, 0.05, 0.1, 0.15, 0.2, 0.25],
        'reg_alpha': [0, 0.1, 0.2, 0.3],
    },
    "LR": {
        "C": [0.001, 0.01, 0.1, 0.5, 1, 2, 5, 10, 25, 50, 100, 500, 1000],
        "class_weight": [None, "balanced"],
        "l1_ratio": [0, 0.05, 0.1, 0.15, 0.2, 0.25, 0.3, 0.35, 0.4, 0.45, 0.5,
                     0.55, 0.6, 0.65, 0.7, 0.75, 0.8, 0.85, 0.9, 0.95, 1]
    },
    "SVM": {
        "C": np.logspace(10e-3, 10e3, num=50),
        "gamma": np.logspace(10e-3, 10e3, num=50),
        "class_weight": [None, "balanced"]
    },
    "RF": {
        "class_weight": [None, "balanced", "balanced_subsample"]
    }
}

## Hyperaktiv Classification

In [16]:
dataset = HYPERAKTIV_PREFIX

In [17]:
# read dataset
# create dictionary with data split for night/day/all and also 6/22, 8/21 day/night
datasets = {}
    
for part in ["full_24h", "night", "day"]:
    for hours in DAY_NIGHT_HOURS:
        filename = f"{dataset}_{hours[0]}_{hours[1]}_{part}.csv"
        filepath = os.path.join(PROCESSED_DATA_DIR, WINDOWS_DIR, filename)
        datasets[part] = pd.read_csv(filepath, header=0).dropna()

In [18]:
results_directory = os.path.join(".", MAIN_RESULTS_DIR, DAY_WINDOWS_DIR, "hyperactiv")
predictions_directory = os.path.join('.', MAIN_RESULTS_DIR, DAY_WINDOWS_DIR, "hyperactiv", "predictions")
os.makedirs(results_directory, exist_ok=True)
os.makedirs(predictions_directory, exist_ok=True)

for part in ["day", "night", "full_24h"]:
    for hours in DAY_NIGHT_HOURS:
        part_hours = f"{part}_{hours[0]}_{hours[1]}"
        if part_hours == "full_24h_6_22":
            break
        print(f"PART: {part_hours}")
        X = datasets[part]
        y = datasets[part]['class']
        print(len(X))
        info = X.iloc[:, -3:]
        group_kfold = GroupKFold(n_splits=5)
        fold_num = 0
        all_predictions = pd.DataFrame()
        
        for train_idx, test_idx in group_kfold.split(X, y, groups=X['patient_id']):
            fold_num += 1 
            X = X.iloc[:, :-3]
            print("fold: ", fold_num)
            
            X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
            y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]
        
            X_train, X_test = variance_thresholding(X_train, X_test, threshold=0.005)
            X_train, X_test = standardize(X_train, X_test)

            for clf_type in ["GBM"]: 

                print(f"    {clf_type}")
                
                test_scores = []
                
                if clf_type == "GBM":
                    model = lightgbm_fit_binary(X_train, y_train)
                else:
                    grid_search = GridSearchCV(
                        estimator=classifiers[clf_type], 
                        param_grid=param_grids[clf_type], 
                        scoring="accuracy",
                        n_jobs=-1,
                        refit=True,
                        cv=LeaveOneOut()
                    )
                    grid_search.fit(X_train, y_train)
                
                    model = grid_search.best_estimator_
                
                y_pred = model.predict(X_test)
                metrics = calculate_metrics(model, X_test, y_test)
                # print(metrics)
                test_scores.append(metrics)
        
                # Save individual fold metrics
                pd.DataFrame.from_records(test_scores).to_csv(
                    os.path.join(results_directory, f"test_scores_{hours[0]}_{hours[1]}_{part}_fold_{clf_type}"),
                    index=False
                )

                predictions_dict = {
                    "fold": [fold_num] * len(y_test),
                    'classifier': [clf_type] * len(y_test),
                    'predicted_class': y_pred,
                    'actual_class': y_test,
                    "patient_id": info.iloc[test_idx]["patient_id"].to_list()
                }
                predictions = pd.DataFrame.from_dict(predictions_dict)
                all_predictions = pd.concat([all_predictions, predictions])
        
                # Compute and save final scores for the fold
                final_scores = calculate_metrics_statistics(test_scores)
                df = pd.DataFrame([(key,) + values for key, values in final_scores.items()],
                                columns=['Index', 'Mean', 'Stddev']).set_index('Index')
                df.to_csv(
                    os.path.join(results_directory, f"final_scores_{hours[0]}_{hours[1]}_{part}_{clf_type}"),
                )
            
                for metric, (mean, stddev) in final_scores.items():
                    print(f"      {metric}: {mean:.4f} +- {stddev:.4f}")
                print()
        
        all_predictions.to_csv(
        os.path.join(predictions_directory, f"predictions_{hours[0]}_{hours[1]}_{part}.csv"),
        index=False
        )


[I 2025-01-16 23:41:36,172] A new study created in memory with name: no-name-ab9ea2a0-4e61-4b3b-a3f1-b84108856dd7


PART: day_8_21
547
fold:  1
    GBM


feature_fraction, val_score: inf:   0%|          | 0/7 [00:00<?, ?it/s]

Training until validation scores don't improve for 100 rounds


feature_fraction, val_score: 0.921339:  14%|#4        | 1/7 [00:00<00:01,  4.11it/s]

...

[100]	cv_agg's valid binary_logloss: 0.97994 + 0.162883
Early stopping, best iteration is:
[5]	cv_agg's valid binary_logloss: 0.922499 + 0.125464
Training until validation scores don't improve for 100 rounds


min_child_samples, val_score: 0.922499:  60%|######    | 3/5 [00:00<00:00,  6.34it/s]

[100]	cv_agg's valid binary_logloss: 0.925432 + 0.133147
Early stopping, best iteration is:
[1]	cv_agg's valid binary_logloss: 0.925432 + 0.133147
Training until validation scores don't improve for 100 rounds
[100]	cv_agg's valid binary_logloss: 0.965751 + 0.158367
Early stopping, best iteration is:
[5]	cv_agg's valid binary_logloss: 0.922662 + 0.125184
Training until validation scores don't improve for 100 rounds


min_child_samples, val_score: 0.922499: 100%|##########| 5/5 [00:00<00:00,  6.57it/s]


[100]	cv_agg's valid binary_logloss: 0.966185 + 0.158498
Early stopping, best iteration is:
[5]	cv_agg's valid binary_logloss: 0.922662 + 0.125184
Training until validation scores don't improve for 100 rounds
[100]	cv_agg's valid binary_logloss: 0.958567 + 0.150256
Early stopping, best iteration is:
[5]	cv_agg's valid binary_logloss: 0.922662 + 0.125184
      accuracy: 0.5278 +- 0.0000
      balanced_accuracy: 0.5390 +- 0.0000
      f1: 0.5641 +- 0.0000
      precision: 0.6600 +- 0.0000
      recall: 0.4925 +- 0.0000
      specificity: 0.5854 +- 0.0000
      ROC_AUC: 0.5390 +- 0.0000
      MCC: 0.0758 +- 0.0000



### Voting

In [20]:
for part in ["day", "night", "full_24h"]:
    for hours in DAY_NIGHT_HOURS:
        part_hours = f"{part}_{hours[0]}_{hours[1]}"
        if part_hours == "full_24h_6_22":
            break
        print(f"PART: {part_hours}")
        predictions = pd.read_csv(os.path.join(predictions_directory, f"predictions_{hours[0]}_{hours[1]}_{part}.csv"))
        predictions["predicted_class"] = (predictions["predicted_class"] > 0.5).astype(int)

        grouped = predictions.groupby(['patient_id', 'classifier'])
        

        most_common_class = (
            grouped['predicted_class']
            .apply(lambda x: x.mode()[0]) 
            .reset_index(name='final_predicted_class')
        )

        final_results = pd.merge(
            most_common_class,
            predictions[['patient_id', 'actual_class']].drop_duplicates(),
            on='patient_id'
        )

        final_results.to_csv(
            os.path.join(predictions_directory, f"final_predictions_{hours[0]}_{hours[1]}_{part}.csv"),
            index=False
        )

        voting_metrics = (
        final_results.groupby('classifier')
        .apply(lambda group: pd.Series(
            calculate_metrics_from_df(group['actual_class'], group['final_predicted_class'])
        ))
        .reset_index()
        )

        display(voting_metrics)
        
        voting_metrics.to_csv(
        os.path.join(predictions_directory, f"voting_scores_{hours[0]}_{hours[1]}_{part}.csv"),
        index=False
        )

PART: day_8_21


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.458824           0.461111  0.452381   0.487179  0.422222   

   specificity   ROC_AUC       MCC  
0          0.5  0.461111 -0.077908

PART: day_6_22


classifier  accuracy  balanced_accuracy   f1  precision    recall  \
0        GBM  0.505882           0.508333  0.5   0.538462  0.466667   

   specificity   ROC_AUC       MCC  
0         0.55  0.508333  0.016695

PART: night_8_21


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.517647           0.522222  0.493827   0.555556  0.444444   

   specificity   ROC_AUC       MCC  
0          0.6  0.522222  0.044896

PART: night_6_22


classifier  accuracy  balanced_accuracy     f1  precision    recall  \
0        GBM  0.505882           0.511111  0.475   0.542857  0.422222   

   specificity   ROC_AUC       MCC  
0          0.6  0.511111  0.022537

PART: full_24h_8_21


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.447059           0.452778  0.405063   0.470588  0.355556   

   specificity   ROC_AUC       MCC  
0         0.55  0.452778 -0.096225

## Depresjon

In [17]:
path = os.path.join(PROCESSED_DATA_DIR, DAY_WINDOWS_DIR, "depresjon")
dataset = DatasetWin(dirpath=path, sep=',')
condition = dataset.condition
control = dataset.control

In [221]:
condition_parts_dfs = extract_features_for_dataframes(condition, freq="H")
control_parts_dfs = extract_features_for_dataframes(control, freq="H")

datasets = {}

for part in ["full_24h", "night", "day"]:
    condition_df = condition_parts_dfs[part]
    control_df = control_parts_dfs[part]
    control_df["class"] = 0
    max_patient = condition_df['patient_id'].max()
    control_df['patient_id'] += max_patient # changing numeration of patients
    entire_df = pd.concat([condition_df, control_df], ignore_index=True)
    datasets[part] = entire_df

In [ ]:
for part, df in datasets.items():
    for hours in DAY_NIGHT_HOURS:
        filename = f"{DEPRESJON_PREFIX}_{hours[0]}_{hours[1]}_{part}.csv"
        filepath = os.path.join(PROCESSED_DATA_DIR, WINDOWS_DIR, filename)
        df.to_csv(filepath, index=False, header=True)

## Depresjon classification

In [21]:
dataset = DEPRESJON_PREFIX

In [22]:
# reading
datasets = {}
  
for part in ["full_24h", "night", "day"]:
    for hours in DAY_NIGHT_HOURS:
        filename = f"{dataset}_{hours[0]}_{hours[1]}_{part}.csv"
        filepath = os.path.join(PROCESSED_DATA_DIR, WINDOWS_DIR, filename)
        datasets[part] = pd.read_csv(filepath, header=0).dropna()

In [23]:
from sklearn.model_selection import StratifiedGroupKFold

results_directory = os.path.join(".", MAIN_RESULTS_DIR, DAY_WINDOWS_DIR, "depresjon")
predictions_directory = os.path.join('.', MAIN_RESULTS_DIR, DAY_WINDOWS_DIR, "depresjon", "predictions")
os.makedirs(results_directory, exist_ok=True)
os.makedirs(predictions_directory, exist_ok=True)
predictions = pd.DataFrame(columns=['fold', 'classifier', 'predicted_class', 'actual_class', 'patient_id'])

for part in ["day", "night", "full_24h"]:
    for hours in DAY_NIGHT_HOURS:
        part_hours = f"{part}_{hours[0]}_{hours[1]}"
        if part_hours == "full_24h_6_22":
            break
        print(f"PART: {part_hours}")
        X = datasets[part]
        y = datasets[part]['class']
        print(len(X))
        info = X.iloc[:, -3:]
        group_kfold = StratifiedGroupKFold(n_splits=5)
        fold_num = 0
        all_predictions = pd.DataFrame()
        
        for train_idx, test_idx in group_kfold.split(X, y, groups=X['patient_id']):
            fold_num += 1 
            X = X.iloc[:, :-3]
            print("fold: ", fold_num)
            
            X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
            y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]
        
            X_train, X_test = variance_thresholding(X_train, X_test, threshold=0.005)
            X_train, X_test = standardize(X_train, X_test)
        
            for clf_type in ["GBM"]: 
                print(f"    {clf_type}")
                
                test_scores = []
                
                if clf_type == "GBM":
                    model = lightgbm_fit_binary(X_train, y_train)
                else:
                    grid_search = GridSearchCV(
                        estimator=classifiers[clf_type], 
                        param_grid=param_grids[clf_type], 
                        scoring="accuracy",
                        n_jobs=-1,
                        refit=True,
                        cv=LeaveOneOut()
                    )
                    grid_search.fit(X_train, y_train)
                
                    model = grid_search.best_estimator_
                y_pred = (model.predict(X_test) > 0.5).astype(int)
                
                metrics = calculate_metrics(model, X_test, y_test)
                # print(metrics)
                test_scores.append(metrics)
        
                # Save individual fold metrics
                pd.DataFrame.from_records(test_scores).to_csv(
                    os.path.join(results_directory, f"test_scores_{hours[0]}_{hours[1]}_{part}_fold_{clf_type}"),
                    index=False
                )

                predictions_dict = {
                    "fold": [fold_num] * len(y_test),
                    'classifier': [clf_type] * len(y_test),
                    'predicted_class': y_pred,
                    'actual_class': y_test,
                    "patient_id": info.iloc[test_idx]["patient_id"].to_list()
                }
                predictions = pd.DataFrame.from_dict(predictions_dict)
                all_predictions = pd.concat([all_predictions, predictions])
        
                # Compute and save final scores for the fold
                final_scores = calculate_metrics_statistics(test_scores)
                df = pd.DataFrame([(key,) + values for key, values in final_scores.items()],
                                columns=['Index', 'Mean', 'Stddev']).set_index('Index')
                df.to_csv(
                    os.path.join(results_directory, f"final_scores_{hours[0]}_{hours[1]}_{part}_{clf_type}"),
                )
            
                for metric, (mean, stddev) in final_scores.items():
                    print(f"      {metric}: {mean:.4f} +- {stddev:.4f}")
                print()
            
        all_predictions.to_csv(
        os.path.join(predictions_directory, f"predictions_{hours[0]}_{hours[1]}_{part}.csv"),
        index=False
        )

[I 2025-01-16 23:57:16,581] A new study created in memory with name: no-name-bde1421d-097f-4d39-b426-6d92da917d85


PART: day_8_21
988
fold:  1
    GBM


feature_fraction, val_score: inf:   0%|          | 0/7 [00:00<?, ?it/s]

Training until validation scores don't improve for 100 rounds


feature_fraction, val_score: 0.839067:  14%|#4        | 1/7 [00:00<00:03,  1.69it/s]

...

min_child_samples, val_score: 0.783131:  80%|########  | 4/5 [00:01<00:00,  3.83it/s]

[100]	cv_agg's valid binary_logloss: 0.876161 + 0.37367
Early stopping, best iteration is:
[14]	cv_agg's valid binary_logloss: 0.794635 + 0.30192
Training until validation scores don't improve for 100 rounds


min_child_samples, val_score: 0.783131: 100%|##########| 5/5 [00:01<00:00,  3.83it/s]

[100]	cv_agg's valid binary_logloss: 0.86419 + 0.381782
Early stopping, best iteration is:
[15]	cv_agg's valid binary_logloss: 0.787934 + 0.30205


      accuracy: 0.6617 +- 0.0000
      balanced_accuracy: 0.6207 +- 0.0000
      f1: 0.5000 +- 0.0000
      precision: 0.5152 +- 0.0000
      recall: 0.4857 +- 0.0000
      specificity: 0.7557 +- 0.0000
      ROC_AUC: 0.6207 +- 0.0000
      MCC: 0.2449 +- 0.0000



### Voting

In [24]:
for part in ["day", "night", "full_24h"]:
    for hours in DAY_NIGHT_HOURS:
        part_hours = f"{part}_{hours[0]}_{hours[1]}"
        if part_hours == "full_24h_6_22":
            break
        print(f"PART: {part_hours}")
        predictions = pd.read_csv(os.path.join(predictions_directory, f"predictions_{hours[0]}_{hours[1]}_{part}.csv"))

        grouped = predictions.groupby(['patient_id', 'classifier'])

        most_common_class = (
            grouped['predicted_class']
            .apply(lambda x: x.mode()[0]) 
            .reset_index(name='final_predicted_class')
        )

        final_results = pd.merge(
            most_common_class,
            predictions[['patient_id', 'actual_class']].drop_duplicates(),
            on='patient_id'
        )

        final_results.to_csv(
            os.path.join(predictions_directory, f"final_predictions_{hours[0]}_{hours[1]}_{part}.csv"),
            index=False
        )

        voting_metrics = (
        final_results.groupby('classifier')
        .apply(lambda group: pd.Series(
            calculate_metrics_from_df(group['actual_class'], group['final_predicted_class'])
        ))
        .reset_index()
        )

        display(voting_metrics)
        
        voting_metrics.to_csv(
        os.path.join(predictions_directory, f"voting_scores_{hours[0]}_{hours[1]}_{part}.csv"),
        index=False
        )

PART: day_8_21


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.727273           0.686141  0.571429   0.833333  0.434783   

   specificity   ROC_AUC       MCC  
0       0.9375  0.686141  0.444618

PART: day_6_22


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.745455           0.713995  0.631579        0.8  0.521739   

   specificity   ROC_AUC       MCC  
0      0.90625  0.713995  0.474019

PART: night_8_21


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.654545           0.617527  0.486486   0.642857  0.391304   

   specificity   ROC_AUC       MCC  
0      0.84375  0.617527  0.266165

PART: night_6_22


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.654545           0.611413  0.457143   0.666667  0.347826   

   specificity   ROC_AUC       MCC  
0        0.875  0.611413  0.266122

PART: full_24h_8_21


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.763636           0.735734  0.666667     0.8125  0.565217   

   specificity   ROC_AUC       MCC  
0      0.90625  0.735734  0.512033

## Psykose

In [223]:
path = os.path.join(PROCESSED_DATA_DIR, DAY_WINDOWS_DIR, "psykose")
dataset = DatasetWin(dirpath=path, sep=',')
condition = dataset.condition
control = dataset.control

In [224]:
condition_parts_dfs = extract_features_for_dataframes(condition, freq="H")
control_parts_dfs = extract_features_for_dataframes(control, freq="H")

datasets = {}

for part in ["full_24h", "night", "day"]:
    condition_df = condition_parts_dfs[part]
    control_df = control_parts_dfs[part]
    control_df["class"] = 0
    max_patient = condition_df['patient_id'].max()
    control_df['patient_id'] += max_patient # changing numeration of patients
    entire_df = pd.concat([condition_df, control_df], ignore_index=True)
    datasets[part] = entire_df

In [ ]:
for part, df in datasets.items():
    for hours in DAY_NIGHT_HOURS:
        filename = f"{PSYKOSE_PREFIX}_{hours[0]}_{hours[1]}_{part}.csv"
        filepath = os.path.join(PROCESSED_DATA_DIR, WINDOWS_DIR, filename)
        df.to_csv(filepath, index=False, header=True)

## Psykose classification

In [25]:
dataset = PSYKOSE_PREFIX

In [26]:
datasets = {}
  
for part in ["full_24h", "night", "day"]:
    for hours in DAY_NIGHT_HOURS:
        filename = f"{dataset}_{hours[0]}_{hours[1]}_{part}.csv"
        filepath = os.path.join(PROCESSED_DATA_DIR, WINDOWS_DIR, filename)
        datasets[part] = pd.read_csv(filepath, header=0).dropna()

In [27]:
from sklearn.model_selection import StratifiedGroupKFold

results_directory = os.path.join(".", MAIN_RESULTS_DIR, DAY_WINDOWS_DIR, "psykose")
predictions_directory = os.path.join('.', MAIN_RESULTS_DIR, DAY_WINDOWS_DIR, "hyperactiv", "predictions")
os.makedirs(results_directory, exist_ok=True)
os.makedirs(predictions_directory, exist_ok=True)
predictions = pd.DataFrame(columns=['fold', 'classifier', 'predicted_class', 'actual_class', 'patient_id'])

for part in ["day", "night", "full_24h"]:
    for hours in DAY_NIGHT_HOURS:
        part_hours = f"{part}_{hours[0]}_{hours[1]}"
        if part_hours == "full_24h_6_22":
            break
        print(f"PART: {part_hours}")
        X = datasets[part]
        y = datasets[part]['class']
        print(len(X))
        info = X.iloc[:, -3:]
        group_kfold = StratifiedGroupKFold(n_splits=5)
        fold_num = 0
        all_predictions = pd.DataFrame()
        
        for train_idx, test_idx in group_kfold.split(X, y, groups=X['patient_id']):
            fold_num += 1 
            X = X.iloc[:, :-3]
            print("fold: ", fold_num)
            
            X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
            y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]
        
            X_train, X_test = variance_thresholding(X_train, X_test, threshold=0.005)
            X_train, X_test = standardize(X_train, X_test)
        
            for clf_type in ["GBM"]: 
                print(f"    {clf_type}")
                
                test_scores = []
                
                if clf_type == "GBM":
                    model = lightgbm_fit_binary(X_train, y_train)
                else:
                    grid_search = GridSearchCV(
                        estimator=classifiers[clf_type], 
                        param_grid=param_grids[clf_type], 
                        scoring="accuracy",
                        n_jobs=-1,
                        refit=True,
                        cv=LeaveOneOut()
                    )
                    grid_search.fit(X_train, y_train)
                
                    model = grid_search.best_estimator_

                
                y_pred = (model.predict(X_test) > 0.5).astype(int)
                metrics = calculate_metrics(model, X_test, y_test)
                # print(metrics)
                test_scores.append(metrics)
                
        
                # Save individual fold metrics
                pd.DataFrame.from_records(test_scores).to_csv(
                    os.path.join(results_directory, f"test_scores_{hours[0]}_{hours[1]}_{part}_fold_{clf_type}"),
                    index=False
                )

                predictions_dict = {
                    "fold": [fold_num] * len(y_test),
                    'classifier': [clf_type] * len(y_test),
                    'predicted_class': y_pred,
                    'actual_class': y_test,
                    "patient_id": info.iloc[test_idx]["patient_id"].to_list()
                }
                predictions = pd.DataFrame.from_dict(predictions_dict)
                all_predictions = pd.concat([all_predictions, predictions])
        
                # Compute and save final scores for the fold
                final_scores = calculate_metrics_statistics(test_scores)
                df = pd.DataFrame([(key,) + values for key, values in final_scores.items()],
                                columns=['Index', 'Mean', 'Stddev']).set_index('Index')
                df.to_csv(
                    os.path.join(results_directory, f"final_scores_{hours[0]}_{hours[1]}_{part}_{clf_type}"),
                )
            
                for metric, (mean, stddev) in final_scores.items():
                    print(f"      {metric}: {mean:.4f} +- {stddev:.4f}")
                print()
            
        all_predictions.to_csv(
        os.path.join(predictions_directory, f"predictions_{hours[0]}_{hours[1]}_{part}.csv"),
        index=False
        )

[I 2025-01-17 00:09:47,240] A new study created in memory with name: no-name-874f6121-eccb-407d-bc8a-12b51fe0fc11


PART: day_8_21
971
fold:  1
    GBM


feature_fraction, val_score: inf:   0%|          | 0/7 [00:00<?, ?it/s]

Training until validation scores don't improve for 100 rounds


feature_fraction, val_score: 0.577038:  14%|#4        | 1/7 [00:00<00:03,  1.67it/s]

...

min_child_samples, val_score: 0.662417:  80%|########  | 4/5 [00:01<00:00,  1.78it/s]

[100]	cv_agg's valid binary_logloss: 1.19645 + 0.706769
Early stopping, best iteration is:
[15]	cv_agg's valid binary_logloss: 0.690537 + 0.282693
Training until validation scores don't improve for 100 rounds


min_child_samples, val_score: 0.662417: 100%|##########| 5/5 [00:02<00:00,  2.13it/s]

[100]	cv_agg's valid binary_logloss: 0.938805 + 0.487604
Early stopping, best iteration is:
[21]	cv_agg's valid binary_logloss: 0.671601 + 0.284727


      accuracy: 0.8410 +- 0.0000
      balanced_accuracy: 0.8257 +- 0.0000
      f1: 0.7634 +- 0.0000
      precision: 0.7463 +- 0.0000
      recall: 0.7812 +- 0.0000
      specificity: 0.8702 +- 0.0000
      ROC_AUC: 0.8257 +- 0.0000
      MCC: 0.6441 +- 0.0000



### Voting

In [28]:
for part in ["day", "night", "full_24h"]:
    for hours in DAY_NIGHT_HOURS:
        part_hours = f"{part}_{hours[0]}_{hours[1]}"
        if part_hours == "full_24h_6_22":
            break
        print(f"PART: {part_hours}")
        predictions = pd.read_csv(os.path.join(predictions_directory, f"predictions_{hours[0]}_{hours[1]}_{part}.csv"))

        grouped = predictions.groupby(['patient_id', 'classifier'])

        most_common_class = (
            grouped['predicted_class']
            .apply(lambda x: x.mode()[0]) 
            .reset_index(name='final_predicted_class')
        )

        final_results = pd.merge(
            most_common_class,
            predictions[['patient_id', 'actual_class']].drop_duplicates(),
            on='patient_id'
        )

        final_results.to_csv(
            os.path.join(predictions_directory, f"final_predictions_{hours[0]}_{hours[1]}_{part}.csv"),
            index=False
        )

        voting_metrics = (
        final_results.groupby('classifier')
        .apply(lambda group: pd.Series(
            calculate_metrics_from_df(group['actual_class'], group['final_predicted_class'])
        ))
        .reset_index()
        )

        display(voting_metrics)
        
        voting_metrics.to_csv(
        os.path.join(predictions_directory, f"voting_scores_{hours[0]}_{hours[1]}_{part}.csv"),
        index=False
        )

PART: day_8_21


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.888889           0.863636  0.842105        1.0  0.727273   

   specificity   ROC_AUC       MCC  
0          1.0  0.863636  0.782586

PART: day_6_22


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.888889           0.863636  0.842105        1.0  0.727273   

   specificity   ROC_AUC       MCC  
0          1.0  0.863636  0.782586

PART: night_8_21


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.814815           0.808239  0.772727   0.772727  0.772727   

   specificity   ROC_AUC       MCC  
0      0.84375  0.808239  0.616477

PART: night_6_22


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.851852           0.846591  0.818182   0.818182  0.818182   

   specificity   ROC_AUC       MCC  
0        0.875  0.846591  0.693182

PART: full_24h_8_21


classifier  accuracy  balanced_accuracy        f1  precision    recall  \
0        GBM  0.851852           0.825284  0.789474     0.9375  0.681818   

   specificity   ROC_AUC       MCC  
0      0.96875  0.825284  0.700047